# Clustering changes?

In [1]:
from ipynb.fs.full.koselleck import *
invalid_words=set()

In [2]:

def get_cdist_change_data(fn=FN_DATA_CDISTMATDF_CACHE,force=False):
    if not force and os.path.exists(fn): return read_df(fn)
    dfpaths=get_model_paths_sattelzeit().set_index('period')

    m1=load_model(dfpaths.loc['1700-1770'].sample(n=1).iloc[0].path)
    m2=load_model(dfpaths.loc['1830-1900'].sample(n=1).iloc[0].path)

    smart_procrustes_align_gensim(m1,m2,combine_models=False)
    
    vocab=m1.wv.index_to_key[:10000]
    wdistvecs1=[
        m1.wv.vectors[m1.wv.key_to_index[w]]
        for w in vocab
    ]
    wdistvecs2=[
        m2.wv.vectors[m2.wv.key_to_index[w]]
        for w in vocab
    ]
    wdistvecs_ch=[
        m2.wv.vectors[m2.wv.key_to_index[w]]-m1.wv.vectors[m1.wv.key_to_index[w]]
        for w in vocab
    ]
    wdistmat1=pd.DataFrame(wdistvecs1,index=vocab)
    wdistmat2=pd.DataFrame(wdistvecs2,index=vocab)
    wdistmat_ch=pd.DataFrame(wdistvecs_ch,index=vocab)
    
    print('Calculating word-change distances (m1)',timer=False)
    cdistmat1=fastdist.cosine_pairwise_distance(wdistmat1.values.astype(float),return_matrix=True)
    print('Calculating word-change distances (m2)')
    cdistmat2=fastdist.cosine_pairwise_distance(wdistmat2.values.astype(float),return_matrix=True)
    print('Calculating word-change distances (m2-m1)')
    cdistmat_ch=fastdist.cosine_pairwise_distance(wdistmat_ch.values.astype(float),return_matrix=True)
    
    print('Gathering in dataframe')
    cdistmatdf1=2-pd.DataFrame(cdistmat1,index=wdistmat1.index,columns=wdistmat1.index)
    cdistmatdf2=2-pd.DataFrame(cdistmat2,index=wdistmat2.index,columns=wdistmat2.index)
    cdistmatdf_ch=2-pd.DataFrame(cdistmat_ch,index=wdistmat_ch.index,columns=wdistmat_ch.index)
    cdistmatdf_ch
    
    cdistmatdfs_cache=[cdistmatdf1,cdistmatdf2,cdistmatdf_ch]
    with open(fn,'wb') as of: pickle.dump(cdistmatdfs_cache, of)
    return cdistmatdfs_cache

In [3]:
cdistmatdf1,cdistmatdf2,cdistmatdf_ch = get_cdist_change_data(force=False)

In [4]:
# cdistmatdf_ch.sort_values('growth').head(25)

In [5]:
# cdistmatdf1.sort_values('growth').head(25)

## combine into ranks

In [6]:
def do_get_cdist_change_ranks(obj):
    o=[]
    w,s1,s2,s_ch,k=obj
    s1=s1.sort_values()
    s2=s2.sort_values()
    s_ch=s_ch.sort_values()
    nbl1=list(s1.index)
    nbl1d={w:i for i,w in enumerate(nbl1)}
    
    nbl2=list(s2.index)
    nbl2d={w:i for i,w in enumerate(nbl2)}
    
    nbl_ch=list(s_ch.index)
    nbl_chd={w:i for i,w in enumerate(nbl_ch)}
    metanb=set(nbl1[:k])|set(nbl2[:k])|set(nbl_ch[:k])
    
    for w2 in metanb:
        odx={
            'word':w,
            'neighbor':w2,
            'rank1':nbl1d.get(w2,np.nan)+1,
            'rank2':nbl2d.get(w2,np.nan)+1,
            'rank_ch':nbl_chd.get(w2,np.nan)+1,
        }
        o+=[odx]
    return pd.DataFrame(o)
    
FN_DATA_CDISTMATDF_CACHE_RANKS=FN_DATA_CDISTMATDF_CACHE.replace('.pkl','.ranks.pkl')
DF_DATA_CDISTMATDF_CACHE_RANKS=None
def get_cdist_change_ranks(fn=FN_DATA_CDISTMATDF_CACHE_RANKS,k=100,num_proc=1,lim=None,force=False):
    global DF_DATA_CDISTMATDF_CACHE_RANKS
    if not force and DF_DATA_CDISTMATDF_CACHE_RANKS is not None: return DF_DATA_CDISTMATDF_CACHE_RANKS
    elif not force and os.path.exists(fn):
        odf=read_df(fn)
    else:
        cdistmatdf1,cdistmatdf2,cdistmatdf_ch=get_cdist_change_data()
        words=list(set(cdistmatdf1.index) & set(cdistmatdf2.index) & set(cdistmatdf_ch.index))
        objs=[
            (
                w,
                cdistmatdf1[w],
                cdistmatdf2[w],
                cdistmatdf_ch[w],
                k
            )
            for w in words[:lim]
        ]
        o=pmap(do_get_cdist_change_ranks,objs,num_proc=num_proc)
        odf=pd.concat(o) if len(o) else pd.DataFrame()
        odf.to_pickle(fn)
    odf=odf.set_index(['word','neighbor']).sort_values(['word','rank_ch'],ascending=[1,1])
    odf['rank_ch_diff']=odf[['rank1','rank2']].min(axis=1)-odf['rank_ch']
    DF_DATA_CDISTMATDF_CACHE_RANKS=odf
    return odf

In [7]:
odf=get_cdist_change_ranks(lim=None,num_proc=4)
odf

rank1  rank2  rank_ch  rank_ch_diff
word neighbor                                     
a'   a'            1      1        1             0
     o'           99      2        2             0
     wi'         106      3        3             0
     nae         499      5        4             1
     hae        1045     51        5            46
...              ...    ...      ...           ...
zs   gd            7    471     9907         -9900
     fid        1620     79     9914         -9835
     kv          980     52     9926         -9874
     uv         1061     40     9936         -9896
     wv           51    720     9972         -9921

[2372971 rows x 4 columns]

In [8]:
odf['rank_ch_diff']=odf[['rank1','rank2']].min(axis=1)-odf['rank_ch']
# odf.sort_values('rank_ch_diff')

In [9]:
# odf.loc['station'].sort_values('rank_ch_diff',ascending=False).head(25)

In [10]:
# odf.query('rank1>100 & rank2>100').loc['culture'].sort_values('rank_ch',ascending=True).head(25)

In [11]:
# odf.loc['growth','progress']

In [12]:
def get_word_simchange(w,min_normal_rank=100,sby='(III)',smin=.75):
    df=get_cdist_change_ranks()
    if w not in set(x for x,y in df.index): return pd.DataFrame()
    dfsimchanges=df.query(f'word=="{w}"').query(f'rank1>{min_normal_rank} & rank2>{min_normal_rank}').sort_values('rank_ch')
    try:
        tdf1=get_tilts_sattelzeit(w).loc[w]
    except KeyError:
        return pd.DataFrame()
    tdf1a,tdf1b=tdf1[tdf1[sby]>smin],tdf1[tdf1[sby]<-smin]
    simvecs=[]
    for w1,w2 in dfsimchanges.index:
        simvec=[]
        try:
            tdf2=get_tilts_sattelzeit(w2).loc[w2]
        except KeyError:
            simvecs+=['']
            continue
        tdf2a,tdf2b=tdf2[tdf2[sby]>smin],tdf2[tdf2[sby]<-smin]
        sharedposvecs={v.split('.')[0] for v in set(tdf1a.index)&set(tdf2a.index)}
        sharednegvecs={v.split('.')[0] for v in set(tdf1b.index)&set(tdf2b.index)}
        for v in sharedposvecs:
            va,vb=v.split('-') if v.count('-') else (v,v)
            simvec.append(f'+{va}')
        for v in sharednegvecs:
            va,vb=v.split('-') if v.count('-') else (v,v)
            vltr='-' if va==vb else '+'
            simvec.append(vltr+vb)
        simvecs.append(' '.join(simvec))
    dfsimchanges['sim_vecs']=simvecs
    return dfsimchanges

def info_word_simchange(w,k=25,**y):
    df=get_word_simchange(w,**y).loc[w]
    for x in df.columns:
        if x.startswith('rank'):
            df[x]=df[x].apply(lambda _: f'{_:,}') if not x.endswith('diff') else df[x].apply(lambda _: f'{_:+,}')
    df=df.iloc[:k]#.set_index('neighbor')
    df=df[['rank_ch','rank1','rank2','rank_ch_diff','sim_vecs']]
    df.columns=[
        'Rank for similarity in change vector',
        'Rank similarity in 1700-1770',
        'Rank similarity in 1830-1900',
        'Rank difference between change vector and actual ranks',
        'Similar vectors of change undergone by the neighbor'
    ]
    return df.rename_axis('Neighbor').to_markdown()


In [13]:
dfx=get_word_simchange('liberal')
dfx

rank1  rank2  rank_ch  rank_ch_diff  \
word    neighbor                                            
liberal peel           7915    194        8           186   
        cabinet        4613    236       11           225   
        leader         4478    170       18           152   
        abolition      4227    167       20           147   
        papal          4006    460       22           438   
...                     ...    ...      ...           ...   
        reformed       2120    132       96            36   
        romish         2561    293       97           196   
        unwilling      1102    805       98           707   
        entertaining    247    809       99           148   
        insurrection   9409   2012      100          1912   

                                               sim_vecs  
word    neighbor                                         
liberal peel          +Strong +Polit +Man +Quant -Ambig  
        cabinet                                  +Polit  
        leader                            +Strong +Freq  
        abolition                  +Active +Pain -Ambig  
        papal                                    +Polit  
...                                                 ...  
        reformed                          +Polit -Ambig  
        romish                                           
        unwilling                                        
        entertaining                             -Ambig  
        insurrection                                     

[62 rows x 5 columns]

In [14]:
printm(info_word_simchange('liberal'))

| Neighbor    |   Rank for similarity in change vector | Rank similarity in 1700-1770   | Rank similarity in 1830-1900   | Rank difference between change vector and actual ranks   | Similar vectors of change undergone by the neighbor   |
|:------------|---------------------------------------:|:-------------------------------|:-------------------------------|:---------------------------------------------------------|:------------------------------------------------------|
| peel        |                                      8 | 7,915                          | 194                            | +186                                                     | +Strong +Polit +Man +Quant -Ambig                     |
| cabinet     |                                     11 | 4,613                          | 236                            | +225                                                     | +Polit                                                |
| leader      |                                     18 | 4,478                          | 170                            | +152                                                     | +Strong +Freq                                         |
| abolition   |                                     20 | 4,227                          | 167                            | +147                                                     | +Active +Pain -Ambig                                  |
| papal       |                                     22 | 4,006                          | 460                            | +438                                                     | +Polit                                                |
| deputation  |                                     23 | 5,783                          | 294                            | +271                                                     | +Neg +Pain                                            |
| dissolution |                                     24 | 7,519                          | 1,283                          | +1,259                                                   | +Polit +Pain -Ambig                                   |
| transaction |                                     25 | 6,564                          | 700                            | +675                                                     | +Active +Polit                                        |
| crisis      |                                     28 | 7,757                          | 1,224                          | +1,196                                                   | +Strong +Polit +Pain                                  |
| policies    |                                     33 | 1,614                          | 484                            | +451                                                     |                                                       |
| cheers      |                                     34 | 2,085                          | 453                            | +419                                                     |                                                       |
| largest     |                                     35 | 5,236                          | 698                            | +663                                                     | -Ambig                                                |
| estimates   |                                     36 | 7,718                          | 224                            | +188                                                     | +Active +Strong                                       |
| pledge      |                                     39 | 2,376                          | 1,190                          | +1,151                                                   | +Active +Pain +Neg +Vice -Ambig                       |
| currency    |                                     40 | 4,549                          | 322                            | +282                                                     |                                                       |
| monopoly    |                                     41 | 3,058                          | 187                            | +146                                                     | +Active +Strong                                       |
| existing    |                                     42 | 6,819                          | 492                            | +450                                                     | +Active +Strong +Freq +Polit +Quant +Pain             |
| proclaim    |                                     43 | 3,353                          | 4,123                          | +3,310                                                   | +Quant +Vice +Pain                                    |
| legislative |                                     45 | 3,884                          | 161                            | +116                                                     | +Pain                                                 |
| agriculture |                                     46 | 122                            | 231                            | +76                                                      | +Polit +Neg +Vice +Pain                               |
| precepts    |                                     47 | 301                            | 1,370                          | +254                                                     | +Pain                                                 |
| cuba        |                                     50 | 9,753                          | 1,003                          | +953                                                     |                                                       |
| resign      |                                     51 | 2,943                          | 1,379                          | +1,328                                                   | +Active +Pain +Neg +Vice -Ambig                       |
| statesmen   |                                     52 | 282                            | 139                            | +87                                                      | +Strong +Polit +Quant +Pain                           |
| landlord    |                                     53 | 3,298                          | 665                            | +612                                                     | +Strong +Polit +Man                                   |

In [15]:
# fdf=get_tilts_sattelzeit(w).loc[w]
# fdf=fdf[fdf['(III)']>1]

# fdf

In [16]:
# format_tilts_sattelzeit_html(w)

In [17]:
words=get_valid_words()[:10]
len(words)

10

In [18]:
FN_ALL_SIMCHANGES=os.path.join(PATH_DATA,'data.all_sim_changes.pkl')
DFALLSIMCHANGES=None

def get_all_simchanges(fn=FN_ALL_SIMCHANGES,words=None,force=False,lim=None,num_proc=1,lim_nbr=100):
    global DFALLSIMCHANGES
    if not force and DFALLSIMCHANGES is not None: return DFALLSIMCHANGES
    odf=pd.DataFrame()
    if not force:
        with get_veclib('simchange') as vl:
            odf=pd.concat(df.assign(word=w) for w,df in tqdm(vl.items())).reset_index().set_index(['word','neighbor'])
    else:
        with get_veclib('simchange') as vl:
            words_done=set(vl.keys())
            print(f'Already have data for {len(words_done)} words')
            words=get_valid_words() if not words else words
            words=[w for w in words if w not in words_done]
            for i,dfg in enumerate(pmap_iter(
                get_word_simchange,
                words[:lim],
                num_proc=num_proc
            )):
                if dfg is None or not len(dfg): continue
                dfg=dfg.query('rank1>100 & rank2>100').sort_values('rank_ch_diff').iloc[:lim_nbr]
                for w,wdf in dfg.groupby('word'): vl[w]=wdf.loc[w]
                if i and not i%25: vl.commit()
            vl.commit()
        odf=get_all_simchanges(force=False)
    DFALLSIMCHANGES=odf
    return odf

In [19]:
# !rm ../db/db.koselleck.simchange.sqlite

In [20]:
odf=get_all_simchanges(lim=None,num_proc=6,force=False)
odf

6851it [00:04, 1521.47it/s]


rank1  rank2  rank_ch  rank_ch_diff sim_vecs
word    neighbor                                                 
long    generation    2427    115       54            61   -Ambig
        along          746    110       13            97         
        straight      3499    153       42           111         
        twilight       741    204       83           121         
        some           274    144       16           128         
...                    ...    ...      ...           ...      ...
bladder christmas     9807   8310       56          8254         
        jubilee       9488   8587       92          8495         
        hospitality   9696   9040       94          8946         
        patriotic     9954   9992       91          9863   +Ambig
        scottish      9997   9982       93          9889         

[504915 rows x 5 columns]

## Cluster

In [21]:
def umap_for_plotting(ddf,suffix=''):
#     print('UMAP for plotting...')
    fit = umap.UMAP().fit_transform(ddf.select_dtypes('number').values)
    dffit=pd.DataFrame(fit,index=ddf.index, columns=['X1'+suffix,'X2'+suffix])#.rename_axis('word_prd')
    #dffit['word']=[x.split('_')[0] for x in dffit.index]
    #dffit['prd']=[x.split('_')[-1] for x in dffit.index]
    return dffit

In [22]:
def umap_for_clustering(ddf,ndim=100,n_neighbors=30,min_dist=0.0,random_state=42,min_samples=None,min_cluster_size=5):
#     print('UMAP for clustering...')
    clusterable_embedding = umap.UMAP(
        n_neighbors=n_neighbors,
        min_dist=min_dist,
        random_state=random_state,
        n_components=ndim,
    ).fit_transform(ddf.select_dtypes('number').values)    
    labels = hdbscan.HDBSCAN(
        min_samples=min_samples,
        min_cluster_size=min_cluster_size,
    ).fit_predict(clusterable_embedding)
    return pd.DataFrame(index=ddf.index).assign(cluster=[f'C{x:02}' for x in labels])


In [23]:
def _umap_simchanges(obj,**kwargs): 
    suf,cdf=obj
    odf=umap_for_plotting(cdf).join(umap_for_clustering(cdf,**kwargs)).rename_axis('word')
    odf.columns=[c+'_'+suf for c in odf.columns]
    return odf

def umap_simchanges(topn=2000,words=None,pos={'n*','j*','v*'},add_words=set(),minwordlen=4,num_proc=1,**kwargs):
    print('Getting words',timer=False)
    if not words:
        chwords=get_changeranks_sattelzeit().index
        novwords=set(get_signif_novelty_words())
        valwords=set(get_valid_words(only_pos=pos)) - set(get_words_anno_invalid())
        okwords=set([w for w in chwords
                     if w in novwords and w in valwords
                     and len(w)>=minwordlen
                    ][:topn])
    else:
        okwords=set(words)
    okwords|=set(add_words)
    
    print('Loading data')
    cdfl = cdistmatdf1,cdistmatdf2,cdistmatdf_ch = [
        cdf.loc[[w for w in cdf.index if w in okwords]][[w for w in cdf.columns if w in okwords]]
        for cdf in get_cdist_change_data(force=False)
    ]
    suffices=['I','II','I-III']
    objs=list(zip(suffices,cdfl))
    o=pmap(_umap_simchanges, objs, num_proc=num_proc)
    odf=pd.concat(o,axis=1) if len(o) else pd.DataFrame()
    odf=odf.join(get_topmost_change(),how='left')
    odf=odf.sort_values('abs(III)',ascending=False).dropna()
    return odf

In [24]:
# # udf_kw=umap_simchanges(words=get_keywords())
# udf=umap_simchanges(topn=1000,num_proc=3)
# udf

In [25]:
# # udf500n=umap_simchanges(topn=500,add_words=get_words_anno_valid(),pos={'n*'})
# # udf500=umap_simchanges(topn=500,add_words=get_words_anno_valid())
# # udf500j=umap_simchanges(topn=500,add_words=get_words_anno_valid(),pos={'j*'})
# # udf1000=umap_simchanges(topn=1000,add_words=get_words_anno_valid()|get_keywords(),pos={'nn1'})
# udf=umap_simchanges(topn=1000,add_words=get_words_anno_valid()|get_keywords(),pos={'nn1','jj'})
# udf

In [26]:
udf5k=umap_simchanges(topn=5000,pos={'nn1'},num_proc=1)
udf5k

[Koselleck] (09:59:48) Getting words 
[Koselleck] (09:59:49) Loading data (+0.9s)
Mapping _umap_simchanges() [x1]: 100%|██████████| 3/3 [00:58<00:00, 19.59s/it]


X1_I      X2_I cluster_I      X1_II     X2_II cluster_II  \
word                                                                      
street     2.933542  7.687562       C44   6.118407  7.885776        C05   
music      6.079913  3.436869       C03   6.283593  9.991931        C00   
fact       8.916449  6.699876       C17  10.025455  8.820339        C-1   
court      7.056321  8.738984       C51   7.073738  6.890133        C02   
majesty    7.529747  8.271199       C32   7.449717  6.269770        C02   
...             ...       ...       ...        ...       ...        ...   
fall       5.056142  5.954742       C06   6.067426  4.490906        C-1   
lawn       3.459122  4.344967       C-1   4.466855  5.395988        C11   
accident   5.310493  6.307337       C-1   8.259299  5.674838        C37   
exile      6.271962  6.723730       C-1   8.953909  5.427219        C-1   
defendant  6.302972  8.797853       C50   7.780147  6.781141        C02   

           X1_I-III  X2_I-III cluster_I-III           vector  1700-1770  \
word                                                                      
street     7.169633  4.068734           C21           Freq.M   3.020047   
music      5.895698  3.313865           C49           Freq.M   0.162359   
fact       4.188359  4.881381           C51           Freq.M   0.048341   
court      8.696046  5.500321           C33           Freq.M  14.568602   
majesty    8.902109  5.532748           C33           Freq.M  10.265567   
...             ...       ...           ...              ...        ...   
fall       7.380527  6.358051           C-1   Time-Space.HGI  -0.348882   
lawn       8.708887  7.030387           C10   Qual-Quant.HGI   1.856784   
accident   5.315948  6.053478           C31  Interp-Desc.HGI  -0.504438   
exile      5.441537  7.896288           C-1  Virtue-Vice.HGI  -0.632170   
defendant  5.855429  6.807875           C-1    Judg-Perc.HGI   0.492685   

                (I)  1770-1830       (II)  1830-1900      (III)   abs(III)  \
word                                                                         
street    -1.645529   1.374518  13.176626  14.551144  11.531097  11.531097   
music      0.950290   1.112648   9.689475  10.802124  10.639765  10.639765   
fact       0.037654   0.085996   9.159712   9.245708   9.197366   9.197366   
court     -4.782928   9.785674  -4.184267   5.601408  -8.967194   8.967194   
majesty   -7.067100   3.198466  -1.593540   1.604926  -8.660641   8.660641   
...             ...        ...        ...        ...        ...        ...   
fall      -0.017809  -0.366691   0.521892   0.155200   0.504083   0.504083   
lawn      -0.171122   1.685662  -0.302230   1.383433  -0.473351   0.473351   
accident  -0.055937  -0.560374   0.529273  -0.031102   0.473336   0.473336   
exile      0.273595  -0.358575  -0.745196  -1.103771  -0.471600   0.471600   
defendant -0.442375   0.050310   0.905700   0.956010   0.463324   0.463324   

          change  
word              
street     +Freq  
music      +Freq  
fact       +Freq  
court      -Freq  
majesty    -Freq  
...          ...  
fall       +Time  
lawn              
accident          
exile             
defendant         

[1467 rows x 18 columns]

In [60]:
from scipy.spatial.distance import euclidean

In [125]:
get_changes_anno(min_count=3).Change.value_counts()

Abstraction                 17
Reification                 11
Collectivisation            11
Concretisation              10
Depoeticisation              9
Economisation                8
Deconcretisation             8
Personalisation              7
Technicalisation             6
Depersonalisation            6
Politicisation               6
Demilitarisation             5
Declassing                   5
Nominalisation               4
Metaphorisation              4
Psychologisation             4
Descientisation              3
Demoralisation               3
Depoliticisation             3
Temporalisation              3
Scientisation                3
Ambiguation                  3
Democratisation              3
Individualisation            3
Counterconceptualisation     3
Evaluation                   3
Musicalisation               3
Name: Change, dtype: int64

In [1]:
# math.

In [3]:
# !killall voila

In [141]:
def plot_change_vecs(words=None,topn=1000,pos={'n*','j*','v*'},udf=None,
                    color='cluster_I-III',x='X1_I-III',y='X2_I-III',shape='cluster_II',remove_unclustered=False,fac=1,
                    lim=None,save=False,title='Top most changing words, arranged by the similarity in their direction of change'):
    udf=umap_simchanges(words=words,topn=topn,pos=pos) if udf is None else udf
    figdf=udf.reset_index()
    figdf[x]=(figdf[x]-figdf[x].mean())/figdf[x].std()
    figdf[y]=(figdf[y]-figdf[y].mean())/figdf[y].std()
    clustered,unclustered = figdf[figdf[color]!='C-1'],figdf[figdf[color]=='C-1']
    clustwords=set(clustered.word)
    
    vdf2a=get_changes_anno(min_count=4).merge(figdf)
#     display(vdf2a.Change.value_counts())
    vdf2=vdf2a.groupby('Change').filter(lambda _: len(_)>=2)
    vdf2=vdf2.groupby('Change').median() * fac
    vdirdf=vdf2a.merge(vdf2,on='Change',suffixes=['_w',''])
#     vdirdf=vdirdf[vdirdf.word.isin(clustwords)]
#     return dict(vdirdf.iloc[0])
    vdirdf['vwdist']=vdirdf.apply(lambda row: euclidean([row[x],row[y]], [row[x+'_w'],row[y+'_w']]),axis=1)
    vdirdf=vdirdf.sort_values('vwdist')
    vdirdf=vdirdf.drop_duplicates('word')
    vdirdf=vdirdf.groupby('Change').head(2).reset_index()
#     return vdirdf.query('Change=="Nominalisation"')
    vdf2['word']=vdf2.index
    invdirdf=set(vdirdf.word)
            
    vdf=get_all_signif_changes()[['change']].merge(figdf,on='word',suffixes=['','_top']).groupby('change').median()*fac
    vdf['word']=vdf.index
            
#     if remove_unclustered:
#         if remove_unclustered is True: remove_unclustered=color
#         figdf=figdf[figdf[remove_unclustered]!='C-1']
        
    figdf=figdf.iloc[:lim]

        
    # plot
    p9.options.figure_size=11,8
    fig=start_fig(
        figdf,
        x=x,
        y=y,
        label='word',
    ) + p9.geom_segment(p9.aes(x=0,y=0,xend=x,yend=y),size=.5,alpha=.25,data=vdf,arrow=p9.geoms.arrow(length=.05,type='closed'),color='darkblue',linetype='solid'
    ) + p9.geom_point(p9.aes(color=color),size=.5,show_legend=False,alpha=.5,data=figdf[figdf[color]!='C-1']
    ) + p9.geom_text(size=4,alpha=.35,data=unclustered[~unclustered.word.isin(invdirdf)]#,fontstyle='italic'#,fontweight=300
    ) + p9.geom_text(size=5,data=clustered[~clustered.word.isin(invdirdf)]#,fontstyle='italic'#,fontweight=300
    ) + p9.geom_label(size=5,data=clustered[clustered.word.isin(invdirdf)]#,fontstyle='italic'#,fontweight=300
    ) + p9.geom_label(size=4,alpha=.5,data=unclustered[unclustered.word.isin(invdirdf)]#,fontstyle='italic'#,fontweight=300
    ) + p9.geom_segment(p9.aes(xend=x+'_w',yend=y+'_w'),size=.5,alpha=.5,data=vdirdf,arrow=p9.geoms.arrow(length=.05,type='closed'),color='darkred',linetype='solid'
    ) + p9.geom_label(size=6,alpha=.75,data=vdf,color='darkblue',fontweight=500,family='monospace'#,label_size=.2
    ) + p9.geom_label(size=6,alpha=.75,data=vdf2,color='darkred',fontstyle='italic',fontweight=400#label_size=.2

    ) + p9.theme_void(
    ) + p9.scale_color_discrete(
    # ) + p9.facet_wrap('cluster_I-III'
    ) + p9.theme(
        title=p9.element_text(size=8),
        plot_background=p9.element_rect(fill='white'),
        axis_title=p9.element_text(size=1,color='white')
    ) + p9.ggtitle(title
    )
    if save: fig.save(os.path.join(PATH_FIGS,'fig.umap_dir_change_v5.png'))
    return fig

In [142]:
plot_change_vecs(udf=udf5k,remove_unclustered=False,save=True)

<ggplot: (8743871394461)>

In [ ]:

f

In [ ]:
plot_change_vecs(udf=udf500,remove_unclustered=True)

In [ ]:
# udf1000n=umap_simchanges(pos={'n*'})
plot_change_vecs(udf=udf1000n,remove_unclustered=True)

In [ ]:
plot_change_vecs(topn=500,pos={'n*'})

In [ ]:
words_anno=set(dfanno[dfanno.is_valid.str.startswith('y')].index)
words_anno

In [ ]:


udf_kw=umap_simchanges(words=get_keywords()|words_anno)
udf_kw

In [ ]:
plot_change_vecs(udf=udf_kw,remove_unclustered=False,color='change')

In [ ]:
# udf2=umap_simchanges??

In [ ]:
udf2=umap_simchanges(topn=1000, min_cluster_size=5)

In [ ]:
udf2

In [ ]:
udf3=umap_simchanges(topn=2000, min_cluster_size=5,add_words=get_keywords())

In [ ]:
set(sdf1.query('change=="+Abs"').index) & set(get_signif_novelty_words())

In [ ]:
plot_change_vecs(udf=udf2,remove_unclustered='cluster_I-III',color='cluster_I')

In [ ]:
plot_change_vecs(udf=udf2,remove_unclustered='cluster_I-III',color='cluster_I')

In [ ]:
# p9.scale_fill_distiller??

In [ ]:
# p9.geom_label??

In [ ]:
p9.scale_fill